In [ ]:
%load_ext autoreload
%autoreload 2

In [10]:
import torch
from torch import nn

import plotly.express as px
from plotly.subplots import make_subplots
import numpy as np

from dataset import DatasetMNIST, load_mnist
from trainer import LitTrainer
from models import CNN

In [9]:
net = torch.load("../checkpoints/pytorch/version_0.pt")
net.eval()

pl_net = LitTrainer.load_from_checkpoint("../checkpoints/lightning_logs/version_26/checkpoints/epoch=9-step=1000.ckpt", model=CNN(1, 10))

In [ ]:
mnist = load_mnist("../downloads/mnist/")
dataset, test_data = DatasetMNIST(*mnist["train"]), DatasetMNIST(*mnist["test"])

In [12]:
def show_sequence(model):
    fig = make_subplots(rows=2, cols=5)

    i, j = 0, np.random.randint(0, 30000)

    while i < 10:
        x, y = dataset[j]
        y_pred = model(x.to("cuda")).detach().cpu()
        p = torch.max(nn.functional.softmax(y_pred, dim=0))
        y_pred = int(np.argmax(y_pred))
        if y_pred == i and p > 0.95:
            img = np.flip(np.array(x.reshape(28, 28)), 0)
            fig.add_trace(px.imshow(img).data[0], row=int(i/5)+1, col=i%5+1)
            i += 1
        j += 1
    fig.show()

In [13]:
print("PyTorch Lightning Network")
show_sequence(pl_net.to("cuda"))
print("Manual Network")
show_sequence(net.to("cuda"))

PyTorch Lightning Network


Manual Network
